In [ ]:
import matplotlib.pyplot as plt
from matplotlib.ticker import FuncFormatter 
from datetime import datetime
import pandas as pd

import mark_backtest_underpar as mark
import globeop_reports as ops

In [ ]:
#exclude sell price that are over 200
df_long = mark.back_test('2013-01-01', '2018-01-01', sell_price_threshold = 200)

In [ ]:
#%matplotlib nbagg
%matplotlib inline
mark.pretty_plot(df_long)
#file saved in serenitas shared drive/edwin/

In [ ]:
#exclude trades that are over 5x mark for purpose of regression
diff_threshold = 5
results = mark.stats(df_long, diff_threshold)

In [ ]:
#Regression Intercept
round(results[0],1)

In [ ]:
#Sale Difference
round(results[1],2)

In [ ]:
#Now Calculate alternate valuation methodologies
df = mark.get_mark_df()

In [ ]:
%matplotlib inline
mark.count_sources(df)

In [ ]:
#difference by source
nav = ops.get_net_navs()['endbooknav']
difference = mark.diff_by_source_percentage(df)
#difference.to_clipboard()

In [ ]:
#plot
ax = difference.plot(kind = 'bar', legend = True, figsize = [10, 3.5])

visible = ax.xaxis.get_ticklabels()[::6]
for label in ax.xaxis.get_ticklabels():
    if label not in visible:
        label.set_visible(False)
        
ax.xaxis.set_major_formatter(plt.FixedFormatter(difference.index.to_series().dt.strftime("%b %Y")))
ax.set_ylabel('NAV Impact vs. Fund Policy (%)')
vals = ax.get_yticks()
ax.set_yticklabels(['{:3.0f}%'.format(x*100) for x in vals])
ax.set_xlabel('')
ax.grid(False, which='major',axis = 'x')
lgd = ax.legend(loc='upper center', bbox_to_anchor=(0.5, -.3),  shadow=True, ncol=5)
ax.figure.savefig("/home/serenitas/edwin/PythonGraphs/Valuation_2.png", bbox_extra_artists=(lgd,), bbox_inches='tight')

In [ ]:
results = mark.alt_navs()

In [ ]:
#%matplotlib nbagg
to_plot = ['mark_closest_all', 'mark_mean_all']
to_plot1 = ['mark_manager']
plot_df0 = results[1][to_plot]
plot_df1 = results[1][to_plot1]

plot_df0 = plot_df0.rename(columns = {'mark_closest_all': 'Third-pary mark closest to LMCG valuation', \
                                    'mark_mean_all': 'Average of all third-party marks'})
plot_df1 = plot_df1.rename(columns = {'mark_manager': 'Marks per fund valuation policy'})

ax = plot_df0.plot(figsize = [10, 3.5])
ax = plot_df1.plot(marker = 'o', ax = ax)
plt.rcParams["font.family"] = "sans-serif"
ax.set_xlabel('')
ax.set_ylabel('NAV', weight = 'bold')
ax.set_title('Fund Return Using Different Valuation Methods', weight = 'bold')
lgd = ax.legend(loc='upper center', bbox_to_anchor=(0.5, -.1),  shadow=True, ncol=3)
ax.figure.savefig("/home/serenitas/edwin/PythonGraphs/Valuation_1.png", bbox_extra_artists=(lgd,), bbox_inches='tight')

In [ ]:
#Fund cumulative returns from the last 12 months
results[1]['mark_manager'][-12:]

In [ ]:
round(mark.annual_performance(results[1])*100,2)

In [ ]:
#A positive impact % means the alternative methodology results in a higher NAV than the fund's valuation policy.
round(pd.DataFrame(mark.alt_nav_impact())*100,2)

In [ ]:
pnl_breakdown = ops.curr_port_PNL()

In [ ]:
#Unrealized MTM Gains/Loss
breakdown_summary = pd.DataFrame(index = {'unreal mark-to-market'}, columns={'Gains','Loss','Net'})
breakdown_summary['Gains'] = pnl_breakdown[pnl_breakdown['mtdbookunrealmtm']>=0].sum()['mtdbookunrealmtm']
breakdown_summary['Loss'] = pnl_breakdown[pnl_breakdown['mtdbookunrealmtm']<0].sum()['mtdbookunrealmtm']
breakdown_summary['Net'] = pnl_breakdown.sum()['mtdbookunrealmtm']

In [ ]:
breakdown_summary / nav[-1]

In [ ]:
df = ops.trade_performance()
df = df.set_index('trade_date')
df.days_held = df.days_held.dt.days
winner = df[df.percent_gain > 0]
df[df.days_held.notnull()].groupby(pd.Grouper(freq='A')).mean()
df